In [0]:
sc

<SparkContext master=spark://10.139.64.4:7077 appName=Databricks Shell>

In [0]:
spark

In [0]:
dbutils.fs.ls("/Volumes/azure_databricks/default/sales/")

[FileInfo(path='dbfs:/Volumes/azure_databricks/default/sales/sales_data_sample.csv', name='sales_data_sample.csv', size=527958, modificationTime=1721797251000)]

In [0]:
df = spark.read.format("csv").option("header","true").option("inferSchema","true").load("dbfs:/Volumes/azure_databricks/default/sales/sales_data_sample.csv"
)

In [0]:
df.show(3)

+-----------+---------------+---------+---------------+-------+--------------+-------+------+--------+-------+-----------+----+-----------+------------------+----------------+--------------------+------------+-----+-----+----------+-------+---------+---------------+----------------+--------+
|ORDERNUMBER|QUANTITYORDERED|PRICEEACH|ORDERLINENUMBER|  SALES|     ORDERDATE| STATUS|QTR_ID|MONTH_ID|YEAR_ID|PRODUCTLINE|MSRP|PRODUCTCODE|      CUSTOMERNAME|           PHONE|        ADDRESSLINE1|ADDRESSLINE2| CITY|STATE|POSTALCODE|COUNTRY|TERRITORY|CONTACTLASTNAME|CONTACTFIRSTNAME|DEALSIZE|
+-----------+---------------+---------+---------------+-------+--------------+-------+------+--------+-------+-----------+----+-----------+------------------+----------------+--------------------+------------+-----+-----+----------+-------+---------+---------------+----------------+--------+
|      10107|             30|     95.7|              2| 2871.0|2/24/2003 0:00|Shipped|     1|       2|   2003|Motorcycles

In [0]:
df.printSchema()

root
 |-- ORDERNUMBER: integer (nullable = true)
 |-- QUANTITYORDERED: integer (nullable = true)
 |-- PRICEEACH: double (nullable = true)
 |-- ORDERLINENUMBER: integer (nullable = true)
 |-- SALES: double (nullable = true)
 |-- ORDERDATE: string (nullable = true)
 |-- STATUS: string (nullable = true)
 |-- QTR_ID: integer (nullable = true)
 |-- MONTH_ID: integer (nullable = true)
 |-- YEAR_ID: integer (nullable = true)
 |-- PRODUCTLINE: string (nullable = true)
 |-- MSRP: integer (nullable = true)
 |-- PRODUCTCODE: string (nullable = true)
 |-- CUSTOMERNAME: string (nullable = true)
 |-- PHONE: string (nullable = true)
 |-- ADDRESSLINE1: string (nullable = true)
 |-- ADDRESSLINE2: string (nullable = true)
 |-- CITY: string (nullable = true)
 |-- STATE: string (nullable = true)
 |-- POSTALCODE: string (nullable = true)
 |-- COUNTRY: string (nullable = true)
 |-- TERRITORY: string (nullable = true)
 |-- CONTACTLASTNAME: string (nullable = true)
 |-- CONTACTFIRSTNAME: string (nullable = tr

In [0]:
df.createOrReplaceTempView("productssales")

In [0]:
spark.sql("select CUSTOMERNAME,SUM(sALES) AS SUM_SALES,SUM(SALES)/(select SUM(SALES) FROM productssales) as contribution_perct from productssales group by CUSTOMERNAME order by SUM_SALES desc").show(10)

+--------------------+------------------+--------------------+
|        CUSTOMERNAME|         SUM_SALES|  contribution_perct|
+--------------------+------------------+--------------------+
|Euro Shopping Cha...| 912294.1100000002| 0.09093270803095634|
|Mini Gifts Distri...|         654858.06| 0.06527282826773756|
|Australian Collec...|200995.40999999997|0.020034171801341955|
|  Muscle Machine Inc|197736.93999999997|0.019709384544809486|
|   La Rochelle Gifts|          180124.9|0.017953908461389938|
|Dragon Souveniers...|172989.68000000008|0.017242707029872822|
|   Land of Toys Inc.|164069.44000000003|0.016353584135627607|
|The Sharp Gifts W...|160010.26999999996| 0.01594898728861078|
|      AV Stores, Co.|157807.80999999997| 0.01572945758877543|
|Anna's Decoration...|153996.13000000003|0.015349529251249026|
+--------------------+------------------+--------------------+
only showing top 10 rows



In [0]:
# FIND SEASONAL SALES CONTRIBUTION
df.select("ORDERDATE").show()

+---------------+
|      ORDERDATE|
+---------------+
| 2/24/2003 0:00|
|  5/7/2003 0:00|
|  7/1/2003 0:00|
| 8/25/2003 0:00|
|10/10/2003 0:00|
|10/28/2003 0:00|
|11/11/2003 0:00|
|11/18/2003 0:00|
| 12/1/2003 0:00|
| 1/15/2004 0:00|
| 2/20/2004 0:00|
|  4/5/2004 0:00|
| 5/18/2004 0:00|
| 6/28/2004 0:00|
| 7/23/2004 0:00|
| 8/27/2004 0:00|
| 9/30/2004 0:00|
|10/15/2004 0:00|
| 11/2/2004 0:00|
|11/15/2004 0:00|
+---------------+
only showing top 20 rows



In [0]:
spark.sql("""SELECT 
             QTR_ID, 
             MONTH_ID, 
             YEAR_ID, 
             SUM(SALES) AS Total_Sales
          FROM 
             productssales
          GROUP BY 
             QTR_ID, 
             MONTH_ID, 
             YEAR_ID
          ORDER BY 
             YEAR_ID,Total_Sales""").show()

+------+--------+-------+------------------+
|QTR_ID|MONTH_ID|YEAR_ID|       Total_Sales|
+------+--------+-------+------------------+
|     1|       1|   2003|          129753.6|
|     1|       2|   2003|140836.19000000003|
|     2|       6|   2003|168082.55999999997|
|     1|       3|   2003|          174504.9|
|     3|       7|   2003|187731.87999999998|
|     2|       5|   2003|         192673.11|
|     3|       8|   2003|          197809.3|
|     2|       4|   2003|201609.55000000002|
|     4|      12|   2003|261876.46000000005|
|     3|       9|   2003|         263973.36|
|     4|      10|   2003|         568290.97|
|     4|      11|   2003|1029837.6600000001|
|     1|       3|   2004|205733.72999999992|
|     2|       4|   2004|206148.12000000008|
|     2|       5|   2004| 273438.3900000001|
|     2|       6|   2004|         286674.22|
|     1|       2|   2004| 311419.5299999999|
|     1|       1|   2004| 316577.4200000001|
|     3|       9|   2004|320750.91000000003|
|     3|  

In [0]:
display(df)

ORDERNUMBER QUANTITYORDERED PRICEEACH ORDERLINENUMBER SALES ORDERDATE STATUS QTR_ID MONTH_ID YEAR_ID PRODUCTLINE MSRP PRODUCTCODE CUSTOMERNAME PHONE ADDRESSLINE1 ADDRESSLINE2 CITY STATE POSTALCODE COUNTRY TERRITORY CONTACTLASTNAME CONTACTFIRSTNAME DEALSIZE 10107 30 95.7 2 2871.0 2/24/2003 0:00 Shipped 1 2 2003 Motorcycles 95 S10_1678 Land of Toys Inc. 2125557818 897 Long Airport Avenue null NYC NY 10022 USA NA Yu Kwai Small 10121 34 81.35 5 2765.9 5/7/2003 0:00 Shipped 2 5 2003 Motorcycles 95 S10_1678 Reims Collectables 26.47.1555 59 rue de l'Abbaye null Reims null 51100 France EMEA Henriot Paul Small 10134 41 94.74 2 3884.34 7/1/2003 0:00 Shipped 3 7 2003 Motorcycles 95 S10_1678 Lyon Souveniers +33 1 46 62 7555 27 rue du Colonel Pierre Avia null Paris null 75508 France EMEA Da Cunha Daniel Medium 10145 45 83.26 6 3746.7 8/25/2003 0:00 Shipped 3 8 2003 Motorcycles 95 S10_1678 Toys4GrownUps.com 6265557265 78934 Hillside Dr. null Pasadena CA 90003 USA NA Young Julie Medium 10159 49 100.0 14 5205.27 10/10/2003 0:00 Shipped 4 10 2003 Motorcycles 95 S10_1678 Corporate Gift Ideas Co. 6505551386 7734 Strong St. null San Francisco CA null USA NA Brown Julie Medium 10168 36 96.66 1 3479.76 10/28/2003 0:00 Shipped 4 10 2003 Motorcycles 95 S10_1678 Technics Stores Inc. 6505556809 9408 Furth Circle null Burlingame CA 94217 USA NA Hirano Juri Medium 10180 29 86.13 9 2497.77 11/11/2003 0:00 Shipped 4 11 2003 Motorcycles 95 S10_1678 Daedalus Designs Imports 20.16.1555 184, chausse de Tournai null Lille null 59000 France EMEA Rance Martine Small 10188 48 100.0 1 5512.32 11/18/2003 0:00 Shipped 4 11 2003 Motorcycles 95 S10_1678 Herkku Gifts +47 2267 3215 Drammen 121, PR 744 Sentrum null Bergen null N 5804 Norway EMEA Oeztan Veysel Medium 10201 22 98.57 2 2168.54 12/1/2003 0:00 Shipped 4 12 2003 Motorcycles 95 S10_1678 Mini Wheels Co. 6505555787 5557 North Pendale Street null San Francisco CA null USA NA Murphy Julie Small 10211 41 100.0 14 4708.44 1/15/2004 0:00 Shipped 1 1 2004 Motorcycles 95 S10_1678 Auto Canal Petit (1) 47.55.6555 25, rue Lauriston null Paris null 75016 France EMEA Perrier Dominique Medium 10223 37 100.0 1 3965.66 2/20/2004 0:00 Shipped 1 2 2004 Motorcycles 95 S10_1678 Australian Collectors, Co. 03 9520 4555 636 St Kilda Road Level 3 Melbourne Victoria 3004 Australia APAC Ferguson Peter Medium 10237 23 100.0 7 2333.12 4/5/2004 0:00 Shipped 2 4 2004 Motorcycles 95 S10_1678 Vitachrome Inc. 2125551500 2678 Kingston Rd. Suite 101 NYC NY 10022 USA NA Frick Michael Small 10251 28 100.0 2 3188.64 5/18/2004 0:00 Shipped 2 5 2004 Motorcycles 95 S10_1678 Tekni Collectables Inc. 2015559350 7476 Moss Rd. null Newark NJ 94019 USA NA Brown William Medium 10263 34 100.0 2 3676.76 6/28/2004 0:00 Shipped 2 6 2004 Motorcycles 95 S10_1678 Gift Depot Inc. 2035552570 25593 South Bay Ln. null Bridgewater CT 97562 USA NA King Julie Medium 10275 45 92.83 1 4177.35 7/23/2004 0:00 Shipped 3 7 2004 Motorcycles 95 S10_1678 La Rochelle Gifts 40.67.8555 67, rue des Cinquante Otages null Nantes null 44000 France EMEA Labrune Janine Medium 10285 36 100.0 6 4099.68 8/27/2004 0:00 Shipped 3 8 2004 Motorcycles 95 S10_1678 Marta's Replicas Co. 6175558555 39323 Spinnaker Dr. null Cambridge MA 51247 USA NA Hernandez Marta Medium 10299 23 100.0 9 2597.39 9/30/2004 0:00 Shipped 3 9 2004 Motorcycles 95 S10_1678 Toys of Finland, Co. 90-224 8555 Keskuskatu 45 null Helsinki null 21240 Finland EMEA Karttunen Matti Small 10309 41 100.0 5 4394.38 10/15/2004 0:00 Shipped 4 10 2004 Motorcycles 95 S10_1678 Baane Mini Imports 07-98 9555 Erling Skakkes gate 78 null Stavern null 4110 Norway EMEA Bergulfsen Jonas Medium 10318 46 94.74 1 4358.04 11/2/2004 0:00 Shipped 4 11 2004 Motorcycles 95 S10_1678 Diecast Classics Inc. 2155551555 7586 Pompton St. null Allentown PA 70267 USA NA Yu Kyung Medium 10329 42 100.0 1 4396.14 11/15/2004 0:00 Shipped 4 11 2004 Motorcycles 95 S10_1678 Land of Toys Inc. 2125557818 897 Long Airport Avenue null NYC NY 10022 USA NA Yu Kwai Medium 10341 41

In [0]:
query = spark.sql("""
  SELECT 
    MONTH_ID,
    CASE 
      WHEN QTR_ID == 1 THEN 'Winter'
      WHEN QTR_ID == 2 THEN 'Spring'
      WHEN QTR_ID == 3 THEN 'Summer'
      ELSE 'Autumn'
    END AS Seasons,
    ROUND(SUM(SALES), 2) AS TOTAL_SALES,
    CUSTOMERNAME
  FROM 
    productssales
  GROUP BY 
    QTR_ID, 
    MONTH_ID, 
    CUSTOMERNAME
  ORDER BY 
    TOTAL_SALES
""")
query.show()

+--------+-------+-----------+--------------------+
|MONTH_ID|Seasons|TOTAL_SALES|        CUSTOMERNAME|
+--------+-------+-----------+--------------------+
|       4| Spring|     553.95|Tokyo Collectable...|
|       8| Summer|     1637.2|        Royale Belge|
|       4| Spring|    1698.78|     Microscale Inc.|
|       4| Spring|    1711.26|        Royale Belge|
|       8| Summer|     2173.6|La Corne D'abonda...|
|      11| Autumn|    2311.68|   Atelier graphique|
|       1| Winter|    2317.44|Marseille Mini Autos|
|       4| Spring|    2587.58|    Handji Gifts& Co|
|      11| Autumn|     2916.2|Technics Stores Inc.|
|       8| Summer|    3127.88|Dragon Souveniers...|
|      10| Autumn|    3220.88|Iberia Gift Impor...|
|       2| Winter|     3987.2|   Boards & Toys Co.|
|       3| Winter|     4175.6|Dragon Souveniers...|
|       4| Spring|     4219.2|  Enaco Distributors|
|      11| Autumn|    4512.48|   Toys4GrownUps.com|
|       9| Summer|     4692.6|Online Mini Colle...|
|       6| S

In [0]:
display(df)

ORDERNUMBER QUANTITYORDERED PRICEEACH ORDERLINENUMBER SALES ORDERDATE STATUS QTR_ID MONTH_ID YEAR_ID PRODUCTLINE MSRP PRODUCTCODE CUSTOMERNAME PHONE ADDRESSLINE1 ADDRESSLINE2 CITY STATE POSTALCODE COUNTRY TERRITORY CONTACTLASTNAME CONTACTFIRSTNAME DEALSIZE 10107 30 95.7 2 2871.0 2/24/2003 0:00 Shipped 1 2 2003 Motorcycles 95 S10_1678 Land of Toys Inc. 2125557818 897 Long Airport Avenue null NYC NY 10022 USA NA Yu Kwai Small 10121 34 81.35 5 2765.9 5/7/2003 0:00 Shipped 2 5 2003 Motorcycles 95 S10_1678 Reims Collectables 26.47.1555 59 rue de l'Abbaye null Reims null 51100 France EMEA Henriot Paul Small 10134 41 94.74 2 3884.34 7/1/2003 0:00 Shipped 3 7 2003 Motorcycles 95 S10_1678 Lyon Souveniers +33 1 46 62 7555 27 rue du Colonel Pierre Avia null Paris null 75508 France EMEA Da Cunha Daniel Medium 10145 45 83.26 6 3746.7 8/25/2003 0:00 Shipped 3 8 2003 Motorcycles 95 S10_1678 Toys4GrownUps.com 6265557265 78934 Hillside Dr. null Pasadena CA 90003 USA NA Young Julie Medium 10159 49 100.0 14 5205.27 10/10/2003 0:00 Shipped 4 10 2003 Motorcycles 95 S10_1678 Corporate Gift Ideas Co. 6505551386 7734 Strong St. null San Francisco CA null USA NA Brown Julie Medium 10168 36 96.66 1 3479.76 10/28/2003 0:00 Shipped 4 10 2003 Motorcycles 95 S10_1678 Technics Stores Inc. 6505556809 9408 Furth Circle null Burlingame CA 94217 USA NA Hirano Juri Medium 10180 29 86.13 9 2497.77 11/11/2003 0:00 Shipped 4 11 2003 Motorcycles 95 S10_1678 Daedalus Designs Imports 20.16.1555 184, chausse de Tournai null Lille null 59000 France EMEA Rance Martine Small 10188 48 100.0 1 5512.32 11/18/2003 0:00 Shipped 4 11 2003 Motorcycles 95 S10_1678 Herkku Gifts +47 2267 3215 Drammen 121, PR 744 Sentrum null Bergen null N 5804 Norway EMEA Oeztan Veysel Medium 10201 22 98.57 2 2168.54 12/1/2003 0:00 Shipped 4 12 2003 Motorcycles 95 S10_1678 Mini Wheels Co. 6505555787 5557 North Pendale Street null San Francisco CA null USA NA Murphy Julie Small 10211 41 100.0 14 4708.44 1/15/2004 0:00 Shipped 1 1 2004 Motorcycles 95 S10_1678 Auto Canal Petit (1) 47.55.6555 25, rue Lauriston null Paris null 75016 France EMEA Perrier Dominique Medium 10223 37 100.0 1 3965.66 2/20/2004 0:00 Shipped 1 2 2004 Motorcycles 95 S10_1678 Australian Collectors, Co. 03 9520 4555 636 St Kilda Road Level 3 Melbourne Victoria 3004 Australia APAC Ferguson Peter Medium 10237 23 100.0 7 2333.12 4/5/2004 0:00 Shipped 2 4 2004 Motorcycles 95 S10_1678 Vitachrome Inc. 2125551500 2678 Kingston Rd. Suite 101 NYC NY 10022 USA NA Frick Michael Small 10251 28 100.0 2 3188.64 5/18/2004 0:00 Shipped 2 5 2004 Motorcycles 95 S10_1678 Tekni Collectables Inc. 2015559350 7476 Moss Rd. null Newark NJ 94019 USA NA Brown William Medium 10263 34 100.0 2 3676.76 6/28/2004 0:00 Shipped 2 6 2004 Motorcycles 95 S10_1678 Gift Depot Inc. 2035552570 25593 South Bay Ln. null Bridgewater CT 97562 USA NA King Julie Medium 10275 45 92.83 1 4177.35 7/23/2004 0:00 Shipped 3 7 2004 Motorcycles 95 S10_1678 La Rochelle Gifts 40.67.8555 67, rue des Cinquante Otages null Nantes null 44000 France EMEA Labrune Janine Medium 10285 36 100.0 6 4099.68 8/27/2004 0:00 Shipped 3 8 2004 Motorcycles 95 S10_1678 Marta's Replicas Co. 6175558555 39323 Spinnaker Dr. null Cambridge MA 51247 USA NA Hernandez Marta Medium 10299 23 100.0 9 2597.39 9/30/2004 0:00 Shipped 3 9 2004 Motorcycles 95 S10_1678 Toys of Finland, Co. 90-224 8555 Keskuskatu 45 null Helsinki null 21240 Finland EMEA Karttunen Matti Small 10309 41 100.0 5 4394.38 10/15/2004 0:00 Shipped 4 10 2004 Motorcycles 95 S10_1678 Baane Mini Imports 07-98 9555 Erling Skakkes gate 78 null Stavern null 4110 Norway EMEA Bergulfsen Jonas Medium 10318 46 94.74 1 4358.04 11/2/2004 0:00 Shipped 4 11 2004 Motorcycles 95 S10_1678 Diecast Classics Inc. 2155551555 7586 Pompton St. null Allentown PA 70267 USA NA Yu Kyung Medium 10329 42 100.0 1 4396.14 11/15/2004 0:00 Shipped 4 11 2004 Motorcycles 95 S10_1678 Land of Toys Inc. 2125557818 897 Long Airport Avenue null NYC NY 10022 USA NA Yu Kwai Medium 10341 41

In [0]:
%sql
select sum(sales) as total_Sales from productssales

total_Sales 1.003262885000001E7

In [0]:
%sql
select count(CUSTOMERNAME) as total_customers from productssales

total_customers 2823

In [0]:
%sql
SELECT SUM(PROFIT) AS TotalProfit
FROM (
  SELECT 
    round(SALES - (PRICEEACH * QUANTITYORDERED),2) AS PROFIT
  FROM 
    productssales
) AS PROFTABLE

TotalProfit 1741742.059999999

In [0]:
%sql
select PRODUCTLINE, sum(QUANTITYORDERED) FROM PRODUCTSSALES
GROUP BY PRODUCTLINE
ORDER BY PRODUCTLINE

PRODUCTLINE sum(QUANTITYORDERED) Classic Cars 33992 Motorcycles 11663 Planes 10727 Ships 8127 Trains 2712 Trucks and Buses 10777 Vintage Cars 21069

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
select MONTH_ID,sum(QUANTITYORDERED) FROM PRODUCTSSALES
group by MONTH_ID
ORDER BY MONTH_ID

MONTH_ID sum(QUANTITYORDERED) 1 7997 2 7903 3 7585 4 6704 5 8992 6 4620 7 4899 8 6538 9 5681 10 10998 11 20857 12 6293

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
select CUSTOMERNAME as customer_name,SUM(sALES) AS SUM_SALES,SUM(SALES)/(select SUM(SALES) FROM productssales) as contribution_perct from productssales group by CUSTOMERNAME order by SUM_SALES desc

customer_name SUM_SALES contribution_perct Euro Shopping Channel 912294.1100000002 0.09093270803095634 Mini Gifts Distributors Ltd. 654858.06 0.06527282826773756 Australian Collectors, Co. 200995.40999999997 0.020034171801341955 Muscle Machine Inc 197736.93999999997 0.019709384544809486 La Rochelle Gifts 180124.9 0.017953908461389938 Dragon Souveniers, Ltd. 172989.68000000008 0.017242707029872822 Land of Toys Inc. 164069.44000000003 0.016353584135627607 The Sharp Gifts Warehouse 160010.26999999996 0.01594898728861078 AV Stores, Co. 157807.80999999997 0.01572945758877543 Anna's Decorations, Ltd 153996.13000000003 0.015349529251249026 Souveniers And Things Co. 151570.98000000004 0.01510780297628571 Corporate Gift Ideas Co. 149882.49999999997 0.014939504116112081 Salzburg Collectables 149798.63 0.014931144392927467 Danish Wholesale Imports 145041.6 0.014456988509048637 Saveley & Henriot, Co. 142874.25000000003 0.01424095839048206 L'ordine Souveniers 142601.33000000002 0.01421375515152241 Rovelli Gifts 137955.72000000003 0.013750705030815515 Reims Collectables 135042.94 0.013460374346450567 Scandinavian Gift Ideas 134259.33000000002 0.013382268197831306 Online Diecast Creations Co. 131685.30000000002 0.013125702342711489 Diecast Classics Inc. 122138.14000000001 0.012174091339978144 Technics Stores Inc. 120783.07 0.012039025045763542 Corrida Auto Replicas, Ltd 120615.28 0.012022300615655674 Tokyo Collectables, Ltd 120562.73999999996 0.012017063703099096 UK Collectables, Ltd. 118008.26999999999 0.011762447486532891 Vida Sport, Ltd 117713.55999999998 0.01173307233427656 Baane Mini Imports 116599.19 0.011621997757845878 Handji Gifts& Co 115498.73000000001 0.011512309657503167 Suominen Souveniers 113961.14999999997 0.011359051720526854 Herkku Gifts 111640.28 0.011127719530858542 Toys of Finland, Co. 111250.37999999996 0.011088856336990862 Mini Creations Ltd. 108951.13 0.01085967911590788 Toys4GrownUps.com 104561.95999999998 0.010422189593906872 Oulu Toy Supplies, Inc. 104370.38 0.010403093900956966 Marta's Replicas Co. 103080.37999999999 0.010274513444200608 Gift Depot Inc. 101894.79000000001 0.010156340030459704 Heintze Collectables 100595.54999999999 0.010026838578803788 Toms Spezialitten, Ltd 100306.58 0.009998035559742638 FunGiftIdeas.com 98923.73000000003 0.009860200300343007 La Corne D'abondance, Co. 97203.68000000001 0.009688754707595896 Amica Models & Co. 94117.26000000002 0.009381116495702911 Cruz & Sons Co. 94015.73 0.009370996516032773 Auto Canal Petit 93170.65999999999 0.009286764355884639 Stylish Desk Decors, Co. 88804.5 0.008851568350402985 Vitachrome Inc. 88041.26000000001 0.008775492576903203 Collectable Mini Designs Co. 87489.22999999998 0.00872046911214102 Mini Classics 85555.98999999998 0.0085277738546064 Blauer See Auto, Co. 85171.58999999998 0.00848945887198846 Motor Mint Distributors Inc. 83682.16 0.008341000275316665 Tekni Collectables Inc. 83228.19 0.008295750918763422 Gifts4AllAges.com 83209.88 0.008293925873675664 Signal Gift Stores 82751.08000000002 0.00824819508797038 Collectables For Less Inc. 81577.98 0.008131266612140238 Mini Caravy 80438.48 0.008017687208672122 Super Scale Inc. 79472.07 0.007921360511607077 Norway Gifts By Mail, Co. 79224.23 0.007896657115946226 Lyon Souveniers 78570.34000000001 0.007831480778838931 Enaco Distributors 78411.86000000002 0.007815684320864708 giftsbymail.co.uk 78240.83999999998 0.007798637941241083 Classic Legends Inc. 77795.2 0.0077542188755442614 Volvo Model Replicas, Co 75754.88 0.007550850443351138 Canadian Gift Exchange Network 75238.92 0.007499422247639502 Petit Auto 74972.52 0.007472868888197725 Marseille Mini Autos 74936.14 0.00746924271996765 Royal Canadian Collectables, Ltd. 74634.84999999999 0.007439211707707089 Mini Wheels Co. 74476.18 0.007423396311526057 Quebec Home Shopping Network 74204.79 0.0073963455749686095 Diecast Collectables 70859.78 0.007062932463608471 Alpha Cognac 70488.44 0.007025919233521723 Daedalus Designs Imports 69052.41 0.006882783269711002 

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
SELECT 
  QTR_ID, 
  SUM(SALES) OVER (PARTITION BY QTR_ID ORDER BY QTR_ID) AS RunningTotalSales
FROM 
  productssales;

QTR_ID RunningTotalSales 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350817.7300000004 1 2350

In [0]:
%sql
SELECT 
  PRODUCTLINE, 
  SUM(SALES) AS TotalSales,
  RANK() OVER (ORDER BY SUM(SALES) DESC) AS SalesRank
FROM 
  productssales
GROUP BY 
  PRODUCTLINE
LIMIT 10;

PRODUCTLINE TotalSales SalesRank Classic Cars 3919615.659999997 1 Vintage Cars 1903150.8399999992 2 Motorcycles 1166388.3400000003 3 Trucks and Buses 1127789.8399999996 4 Planes 975003.5700000001 5 Ships 714437.13 6 Trains 226243.46999999997 7

In [0]:
%sql
SELECT 
  YEAR_ID, 
  SUM(SALES) AS TotalSales,
  LAG(SUM(SALES), 1, 0) OVER (ORDER BY YEAR_ID) AS PrevYearSales,
  ROUND((SUM(SALES)-LAG(SUM(SALES), 1, 0) OVER (ORDER BY YEAR_ID)) / LAG(SUM(SALES), 1, 0) OVER (ORDER BY YEAR_ID) * 100,2) AS SalesGrowth
FROM 
  productssales
GROUP BY 
  YEAR_ID;

YEAR_ID TotalSales PrevYearSales SalesGrowth 2003 3516979.540000001 0.0 null 2004 4724162.599999997 3516979.540000001 34.32 2005 1791486.71 4724162.599999997 -62.08

In [0]:
%sql
WITH ranked_products AS (
  SELECT 
    QTR_ID, PRODUCTCODE, 
    SUM(SALES) AS TotalSales,
    RANK() OVER (PARTITION BY QTR_ID ORDER BY SUM(SALES) DESC) AS SalesRank
  FROM 
    productssales
  GROUP BY 
    QTR_ID, 
    PRODUCTCODE
)
SELECT QTR_ID, PRODUCTCODE, TotalSales,SalesRank
FROM ranked_products
WHERE SalesRank <= 3
ORDER BY QTR_ID, SalesRank;

QTR_ID PRODUCTCODE TotalSales SalesRank 1 S18_3232 54246.03999999999 1 1 S12_1108 42518.53999999999 2 1 S10_1949 40338.53999999999 3 2 S18_3232 70189.43000000001 1 2 S10_4698 52808.69 2 2 S18_2238 38806.13 3 3 S18_3232 50352.01 1 3 S12_1099 39477.92 2 3 S10_1949 38424.0 3 4 S18_3232 113457.93999999999 1 4 S10_1949 75039.22 2 4 S18_2238 61796.48999999999 3

In [0]:
%sql
SELECT 
  ProductLine,
  QTR_ID,
  CASE
    WHEN quantity = max_qty THEN 'hot'
    WHEN quantity = min_qty THEN 'cold'
    ELSE 'median'
  END AS Category
FROM (
  SELECT 
    ProductLine,
    QTR_ID,
    SUM(QUANTITYORDERED) AS quantity,
    MAX(SUM(QUANTITYORDERED)) OVER (PARTITION BY QTR_ID) AS max_qty,
    MIN(SUM(QUANTITYORDERED)) OVER (PARTITION BY QTR_ID) AS min_qty
  FROM PRODUCTSSALES
  GROUP BY ProductLine, QTR_ID
) AS fact
GROUP BY ProductLine, QTR_ID, Category
HAVING Category = 'hot' OR Category = 'cold'
ORDER BY QTR_ID;

ProductLine QTR_ID Category Classic Cars 1 hot Trains 1 cold Classic Cars 2 hot Trains 2 cold Classic Cars 3 hot Trains 3 cold Trains 4 cold Classic Cars 4 hot

In [0]:
%sql
-- identify product WITH OUTLIERS SALES IN EACH QUARTER
WITH QUARTILES AS( 
  select
      QTR_ID,
      PRODUCTCODE,
      PERCENTILE_CONT(0.25) WITHIN GROUP (ORDER BY SALES) AS Q1,
      PERCENTILE_CONT(0.75) WITHIN GROUP (ORDER BY SALES) AS Q3
    FROM productssales
    group by QTR_ID,PRODUCTCODE
),

OutliersBounds AS (
  SELECT 
      QTR_ID,
      PRODUCTCODE,
      Q1,Q3,
      (Q1 - 1.5*(Q3 - Q1)) AS UpperBound,
      (Q3 - 1.5*(Q3 - Q1)) AS LowerBound
  from Quartiles
)
select 
    s.QTR_ID,
    s.PRODUCTCODE,
    s.SALES,
    ob.UpperBound,
    ob.LowerBound
from productssales s
JOIN OutliersBounds ob
on s.QTR_ID =OB.QTR_ID AND s.PRODUCTCODE = ob.PRODUCTCODE
WHERE s.SALES > ob.UpperBound or s.SALES < ob.LowerBound


QTR_ID PRODUCTCODE SALES UpperBound LowerBound 1 S18_2248 1331.1 -1031.0625000000002 559.1624999999999 3 S24_4278 1666.35 1114.5862499999998 1453.2037499999997 1 S12_3148 4071.85 1679.156250000001 3381.2437500000005 1 S18_2625 6981.0 201.41624999999976 936.0987499999999 3 S18_2625 1550.72 945.1499999999996 1308.4499999999998 1 S24_2841 1611.4 741.9962500000006 1773.3787500000003 2 S24_3420 1254.6 710.65 1252.7199999999998 1 S32_2206 1826.96 969.2137500000001 1459.45625 4 S50_1341 2725.47 304.49000000000046 1179.7500000000002 1 S10_1678 3207.12 1229.0100000000002 2323.67 1 S18_4409 3376.64 1093.2275 2063.6825 1 S24_3969 4086.29 1345.9687500000002 1491.7762500000001 3 S24_2840 1172.34 413.625 731.895 4 S24_4620 2670.92 147.79500000000007 1562.545 1 S700_1138 2600.13 1307.414999999999 1931.4349999999995 4 S32_4485 4326.8 -66.00000000000045 1654.3999999999996 4 S12_1666 5960.36 133.5325000000007 2592.1075 3 S18_3140 2819.28 52.430000000000746 2445.1900000000005 2 S700_3167 2620.8 1968.7000000000012 2457.3000000000006 1 S18_1129 3375.72 2208.5487499999995 3121.8312499999997 1 S24_1046 3441.82 -1892.6399999999999 214.30000000000018 2 S700_1138 2639.58 939.5150000000003 1591.005 4 S18_1889 3599.75 -359.493750000001 1280.7987499999995 1 S24_2887 1596.76 465.3899999999999 2015.4299999999998 2 S12_3380 1092.2 239.6450000000009 1463.3350000000005 4 S18_4600 3559.64 -1014.0325000000003 1809.1224999999995 2 S18_4933 2078.28 601.9887500000002 1426.8112500000002 2 S18_1342 4873.05 1035.24375 2513.89125 1 S18_2581 2613.92 1242.4650000000001 2206.005 2 S32_4289 1591.72 1252.8125 1996.7675 4 S700_4002 4277.35 1574.7637499999996 2309.12625 3 S32_3207 2099.63 886.5500000000004 1695.2700000000002 1 S10_4962 1735.3 -1885.75875 1419.6487500000003 4 S18_3136 5160.76 -1085.7149999999997 1220.1350000000002 3 S18_4027 7140.76 2466.5999999999995 3349.88 3 S24_2841 1496.25 548.4000000000001 1255.27 2 S700_3962 2439.99 774.9000000000003 1966.5000000000002 2 S18_1367 1293.75 599.0949999999998 1040.6399999999999 3 S18_4600 5288.64 3428.3799999999997 4210.26 2 S24_4278 3581.76 1189.4274999999993 2143.1924999999997 1 S32_4289 1483.02 -751.5675000000006 875.5274999999997 3 S10_4757 3427.2 2249.439999999999 2962.0799999999995 1 S24_2840 1789.4 -3786.6000000000013 -429.28000000000065 2 S12_4473 4692.6 3125.4874999999997 4233.0725 3 S18_2949 5713.79 2395.0099999999998 3655.31 3 S24_3432 4873.26 3242.9474999999998 4095.8624999999997 3 S32_4289 2234.4 333.0999999999999 1279.48 2 S10_4698 9218.16 4602.491249999996 6462.768749999998 4 S18_3856 3374.6 1917.361249999999 3042.7387499999995 3 S24_2022 2177.1 1948.8224999999998 2087.6575 4 S24_2887 2093.76 -373.49999999999955 1472.7000000000003 1 S18_1662 4215.09 -2758.40625 588.7462500000001 2 S18_3140 4872.03 1789.34625 3089.61875 4 S32_3207 4301.22 607.4899999999996 1749.9399999999998 4 S700_2834 3186.48 3179.250000000001 3588.675 4 S12_3891 3042.41 -2634.9424999999997 1280.0625 3 S18_3259 2418.24 -216.78000000000065 1539.8999999999996 3 S18_3856 1863.4 647.4099999999999 2254.25 4 S18_3232 2991.68 -1104.2000000000003 2296.2 2 S24_4258 2208.92 2497.5874999999996 2934.2824999999993 2 S10_1949 12001.0 3779.89 5340.1900000000005 2 S10_2016 5887.35 -579.0700000000011 1978.3499999999995 2 S700_2466 2457.18 721.8750000000005 2100.4750000000004 4 S12_1099 3584.25 -148.14499999999907 2526.135 3 S18_1984 3516.48 1473.045 2993.715 4 S24_1046 1726.37 637.7437499999996 1399.8562499999998 2 S24_1785 4165.61 1555.2800000000016 2537.9100000000008 4 S12_3380 4220.92 442.69249999999965 2338.8875 1 S18_2325 3068.69 2387.0349999999994 3257.7549999999997 4 S18_3482 3177.91 1453.0050000000006 2786.195 4 S18_4522 3023.1 1106.9999999999998 2384.3999999999996 1 S18_2949 1448.0 -741.7274999999995 1335.1875 4 S700_1138 3526.82 335.3399999999999 1327.78 3 S10_2016 3757.26 480.00000000000045 2365.1800000000003 3 S24_1046 2381.04 1505.9524999999994 1943.5874999999996 3 S12_4675 2675.13 2251.4700000000003 2643.0299999999997 2 S18_1749 5283.6 -2136.26

Rolling 3 month sales average for each product

In [0]:
%sql
SELECT
         YEAR_ID,
         MONTH_ID,
         PRODUCTCODE,
         SALES,
         AVG(SALES) OVER (PARTITION BY PRODUCTCODE ORDER BY YEAR_ID, MONTH_ID ROWS BETWEEN 3 PRECEDING AND CURRENT 
         ROW) AS MOVING_AVG_3_MONTHS
FROM productssales
ORDER BY PRODUCTCODE, YEAR_ID, MONTH_ID

YEAR_ID MONTH_ID PRODUCTCODE SALES MOVING_AVG_3_MONTHS 2003 2 S10_1678 2871.0 2871.0 2003 5 S10_1678 2765.9 2818.45 2003 7 S10_1678 3884.34 3173.7466666666664 2003 8 S10_1678 3746.7 3316.9849999999997 2003 10 S10_1678 5205.27 3900.5525 2003 10 S10_1678 3479.76 4079.0175000000004 2003 11 S10_1678 2497.77 3732.3750000000005 2003 11 S10_1678 5512.32 4173.780000000001 2003 12 S10_1678 2168.54 3414.5975 2004 1 S10_1678 4708.44 3721.7675 2004 2 S10_1678 3965.66 4088.74 2004 4 S10_1678 2333.12 3293.9399999999996 2004 5 S10_1678 3188.64 3548.9649999999992 2004 6 S10_1678 3676.76 3291.045 2004 7 S10_1678 4177.35 3343.9675 2004 8 S10_1678 4099.68 3785.6075 2004 9 S10_1678 2597.39 3637.795 2004 10 S10_1678 4394.38 3817.2 2004 11 S10_1678 7737.93 5221.6225 2004 11 S10_1678 4358.04 3862.3725000000004 2004 11 S10_1678 4396.14 3936.4875 2004 12 S10_1678 1451.0 4485.7775 2005 2 S10_1678 733.11 3579.545 2005 3 S10_1678 3207.12 3282.29 2005 4 S10_1678 2434.56 1956.4474999999998 2005 5 S10_1678 7516.08 3472.7174999999997 2003 1 S10_1949 5404.62 5404.62 2003 3 S10_1949 7209.11 6306.865 2003 5 S10_1949 7329.06 6647.596666666667 2003 7 S10_1949 7374.1 6829.2225 2003 9 S10_1949 10993.5 8226.442500000001 2003 10 S10_1949 4860.24 7639.225 2003 11 S10_1949 5372.57 7310.282499999999 2003 11 S10_1949 7290.36 6384.4974999999995 2003 11 S10_1949 8014.82 7810.664999999999 2003 12 S10_1949 9064.89 7435.66 2004 1 S10_1949 6075.3 6950.78 2004 3 S10_1949 6463.23 7223.445 2004 5 S10_1949 6120.34 6930.94 2004 6 S10_1949 7680.64 6584.8775 2004 7 S10_1949 4905.39 6292.4 2004 8 S10_1949 8014.82 6680.2975 2004 9 S10_1949 7136.19 6934.259999999999 2004 10 S10_1949 10172.7 7557.275 2004 10 S10_1949 11623.7 9236.8525 2004 11 S10_1949 3944.7 6142.95 2004 11 S10_1949 6000.4 8733.2475 2004 11 S10_1949 3003.0 7699.950000000001 2004 12 S10_1949 5691.84 4659.985 2005 1 S10_1949 4514.92 4288.615 2005 2 S10_1949 8254.8 5601.5650000000005 2005 3 S10_1949 2416.56 5219.53 2005 5 S10_1949 4140.23 4831.6275 2005 5 S10_1949 12001.0 6703.147499999999 2003 2 S10_2016 3896.49 3896.49 2003 4 S10_2016 2793.86 3345.175 2003 7 S10_2016 3307.77 3332.706666666667 2003 8 S10_2016 5192.95 3797.7675 2003 10 S10_2016 5016.83 4077.8525 2003 10 S10_2016 3660.93 4294.62 2003 11 S10_2016 4695.6 4641.577499999999 2003 11 S10_2016 3660.92 4258.57 2003 12 S10_2016 3025.92 3760.8425 2004 1 S10_2016 3009.09 3597.8825 2004 2 S10_2016 5422.39 3779.58 2004 4 S10_2016 2852.08 3577.3700000000003 2004 5 S10_2016 5756.52 4260.02 2004 6 S10_2016 4472.0 4625.7475 2004 7 S10_2016 2904.44 3996.26 2004 8 S10_2016 6484.59 4904.387500000001 2004 9 S10_2016 3757.26 4404.5725 2004 10 S10_2016 4043.96 4297.5625 2004 11 S10_2016 5566.5 4963.0775 2004 11 S10_2016 3176.0 4135.93 2004 11 S10_2016 2756.8 3885.8149999999996 2004 12 S10_2016 1329.9 3207.2999999999997 2005 2 S10_2016 5288.01 3137.6775000000002 2005 3 S10_2016 2225.5 2900.0525000000002 2005 4 S10_2016 5833.8 3669.3025 2005 5 S10_2016 5887.35 4808.665000000001 2003 2 S10_4698 6065.55 6065.55 2003 4 S10_4698 9264.86 7665.205 2003 7 S10_4698 7023.98 7451.463333333333 2003 8 S10_4698 5176.38 6882.6925 2003 10 S10_4698 4132.7 6399.4800000000005 2003 10 S10_4698 4183.0 5129.015 2003 11 S10_4698 8892.9 5596.245 2003 11 S10_4698 8714.7 6480.825 2003 12 S10_4698 8065.89 7464.1224999999995 2004 1 S10_4698 6123.4 7949.2225 2004 2 S10_4698 9774.03 8169.504999999999 2004 4 S10_4698 7023.9 7746.805 2004 5 S10_4698 7078.23 7499.89 2004 6 S10_4698 8336.94 8053.275 2004 7 S10_4698 6901.92 7335.2474999999995 2004 8 S10_4698 5438.07 6938.79 2004 9 S10_4698 6683.34 6840.0675 2004 10 S10_4698 4570.4 5898.432500000001 2004 11 S10_4698 5868.2 6197.27 2004 11 S10_4698 2990.13 5273.967500000001 2004 11 S10_4698 7667.14 6089.737499999999 2005 1 S10_4698 3664.1 5047.3925 2005 2 S10_4698 3834.38 4089.2025000000003 2005 3 S10_4698 1822.17 3077.695 2005 4 S10_4698 11886.6 5301.8125 2005 5 S10_4698 9218.16 6690.3275 2003 2 S10_4757 7208.0 7208.0 2003 4 S10_4757 5004.8 6106.4 2003 6 S10_4757 439

In [0]:
%sql
-- Yearly sales performance for each territory
select
    YEAR_ID,
    TERRITORY,
    SUM(SALES) AS TOTAL_SALES
FROM productssales
GROUP BY YEAR_ID,TERRITORY
ORDER BY TERRITORY,YEAR_ID


YEAR_ID TERRITORY TOTAL_SALES 2003 APAC 253134.45000000004 2004 APAC 345307.8299999998 2005 APAC 147679.55000000002 2003 EMEA 1660314.5300000005 2004 EMEA 2389128.889999999 2005 EMEA 929828.9899999998 2003 Japan 243773.18 2004 Japan 168479.09999999992 2005 Japan 42920.939999999995 2003 NA 1359757.3799999997 2004 NA 1821246.779999999 2005 NA 671057.2300000002

In [0]:
%sql
-- Yearly sales performance for each territory
select
    YEAR_ID,
    TERRITORY,
    SUM(SALES) AS TOTAL_SALES,
    AVG(SUM(SALES)) OVER(PARTITION BY TERRITORY ORDER BY YEAR_ID ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW) AS
    AVG_SALES,
    MAX(SUM(SALES)) OVER(PARTITION BY TERRITORY ORDER BY YEAR_ID ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW) AS MAX_SALES
FROM productssales
GROUP BY YEAR_ID, TERRITORY
ORDER BY TERRITORY, YEAR_ID

YEAR_ID TERRITORY TOTAL_SALES AVG_SALES MAX_SALES 2003 APAC 253134.45000000004 253134.45000000004 253134.45000000004 2004 APAC 345307.8299999998 299221.1399999999 345307.8299999998 2005 APAC 147679.55000000002 248707.2766666666 345307.8299999998 2003 EMEA 1660314.5300000005 1660314.5300000005 1660314.5300000005 2004 EMEA 2389128.889999999 2024721.71 2389128.889999999 2005 EMEA 929828.9899999998 1659757.47 2389128.889999999 2003 Japan 243773.18 243773.18 243773.18 2004 Japan 168479.09999999992 206126.13999999996 243773.18 2005 Japan 42920.939999999995 151724.40666666665 243773.18 2003 NA 1359757.3799999997 1359757.3799999997 1359757.3799999997 2004 NA 1821246.779999999 1590502.0799999994 1821246.779999999 2005 NA 671057.2300000002 1284020.463333333 1821246.779999999

FIND OUT THE MONTHLY ORDERS PERFORMANCE OF EACH PRODUCTLINE -SUM,MEDIAN,VARIANCE AVERAGE,MAX

In [0]:
%sql
SELECT 
    MONTH_ID,
    PRODUCTLINE,
    SUM(QUANTITYORDERED) AS TOTAL_QUANTITY,
    percentile_approx(QUANTITYORDERED,0.5) AS MEDIAN,
    variance(SUM(QUANTITYORDERED)) OVER (PARTITION BY PRODUCTLINE ORDER BY MONTH_ID ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW) AS VARIANCE,
    AVG(SUM(QUANTITYORDERED)) OVER (PARTITION BY PRODUCTLINE ORDER BY MONTH_ID ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW) AS AVG,
    MAX(SUM(QUANTITYORDERED)) OVER (PARTITION BY PRODUCTLINE ORDER BY MONTH_ID ROWS BETWEEN UNBOUNDED PRECEDING AND CURRENT ROW) AS MAX_SUM
FROM productssales
GROUP BY MONTH_ID,PRODUCTLINE
ORDER BY PRODUCTLINE,MONTH_ID


MONTH_ID PRODUCTLINE TOTAL_QUANTITY MEDIAN VARIANCE AVG MAX_SUM 1 Classic Cars 2740 35 null 2740.0 2740 2 Classic Cars 2586 35 11858.0 2663.0 2740 3 Classic Cars 2458 37 19937.333333333336 2594.6666666666665 2740 4 Classic Cars 2310 43 33550.333333333314 2523.5 2740 5 Classic Cars 3057 35 82087.19999999998 2630.2 3057 6 Classic Cars 1080 30 466189.7666666666 2371.8333333333335 3057 7 Classic Cars 2028 36 405380.23809523805 2322.714285714286 3057 8 Classic Cars 2224 34 348686.8392857142 2310.375 3057 9 Classic Cars 1938 30 320507.9999999999 2269.0 3057 10 Classic Cars 3818 33 524836.1000000001 2423.9 3818 11 Classic Cars 7548 33 2859298.0181818185 2889.7272727272725 7548 12 Classic Cars 2205 36 2638432.7878787885 2832.6666666666665 7548 1 Motorcycles 837 36 null 837.0 837 2 Motorcycles 1151 37 49298.0 994.0 1151 3 Motorcycles 683 39 56889.33333333333 890.3333333333334 1151 4 Motorcycles 1152 32 55043.58333333332 955.75 1152 5 Motorcycles 1053 35 43174.19999999999 975.2 1152 6 Motorcycles 516 37 69683.46666666666 898.6666666666666 1152 7 Motorcycles 622 31 69004.4761904762 859.1428571428571 1152 8 Motorcycles 1115 37 67329.55357142857 891.125 1152 9 Motorcycles 477 32 77968.86111111112 845.1111111111111 1152 10 Motorcycles 1054 31 73669.11111111112 866.0 1152 11 Motorcycles 2521 37 315304.4727272728 1016.4545454545455 2521 12 Motorcycles 482 30 310443.90151515155 971.9166666666666 2521 1 Planes 588 31 null 588.0 588 2 Planes 1154 36 160178.0 871.0 1154 3 Planes 883 36 80137.0 875.0 1154 4 Planes 1171 32 75328.66666666667 949.0 1171 5 Planes 807 35 60529.3 920.6 1171 6 Planes 795 34 51052.66666666667 899.6666666666666 1171 7 Planes 434 35 73521.80952380954 833.1428571428571 1171 8 Planes 755 30 63781.98214285715 823.375 1171 9 Planes 360 25 79666.61111111112 771.8888888888889 1171 10 Planes 1115 35 82587.28888888888 806.2 1171 11 Planes 1898 34 182694.67272727267 905.4545454545455 1898 12 Planes 767 35 167683.5378787878 893.9166666666666 1898 1 Ships 652 37 null 652.0 652 2 Ships 722 31 2450.0 687.0 722 3 Ships 789 36 4693.0 721.0 789 4 Ships 399 38 29049.666666666668 640.5 789 5 Ships 608 32 21998.5 634.0 789 6 Ships 613 34 17672.3 630.5 789 7 Ships 267 26 33602.95238095238 578.5714285714286 789 8 Ships 629 38 29120.410714285714 584.875 789 9 Ships 520 34 25948.0 577.6666666666666 789 10 Ships 957 35 37454.26666666667 615.6 957 11 Ships 1668 35 134394.81818181818 711.2727272727273 1668 12 Ships 303 28 136067.6590909091 677.25 1668 1 Trains 238 30 null 238.0 238 2 Trains 219 30 180.5 228.5 238 3 Trains 236 43 109.0 231.0 238 4 Trains 69 21 6633.666666666667 190.5 238 5 Trains 254 42 5781.7 203.2 254 6 Trains 116 41 5892.666666666666 188.66666666666666 254 7 Trains 135 45 5321.999999999999 181.0 254 8 Trains 215 36 4706.214285714285 185.25 254 9 Trains 181 31 4119.944444444444 184.77777777777777 254 10 Trains 348 38 6326.322222222222 201.1 348 11 Trains 497 32 13653.4 228.0 497 12 Trains 204 27 12460.181818181818 226.0 497 1 Trucks and Buses 753 31 null 753.0 753 2 Trucks and Buses 680 35 2664.5 716.5 753 3 Trucks and Buses 635 32 3546.333333333333 689.3333333333334 753 4 Trucks and Buses 279 32 44457.583333333336 586.75 753 5 Trucks and Buses 1433 37 176571.0 756.0 1433 6 Trucks and Buses 574 41 146777.46666666667 725.6666666666666 1433 7 Trucks and Buses 637 34 123437.66666666667 713.0 1433 8 Trucks and Buses 487 29 112188.21428571429 684.75 1433 9 Trucks and Buses 825 41 100350.25 700.3333333333334 1433 10 Trucks and Buses 1206 36 114770.1 750.9 1433 11 Trucks and Buses 2290 38 318641.16363636364 890.8181818181819 2290 12 Trucks and Buses 978 37 290307.17424242425 898.0833333333334 2290 1 Vintage Cars 2189 36 null 2189.0 2189 2 Vintage Cars 1391 39 318402.0 1790.0 2189 3 Vintage Cars 1901 33 163308.0 1827.0 2189 4 Vintage Cars 1324 36 172124.25 1701.25 2189 5 Vintage Cars 1780 36 130333.5 1717.0 2189 6 Vintage Cars 926 37 208546.96666666665 1585.1666666666667 2189 7 Vintage Cars 776 32 267324.95238095237 1469.5714285714287 2189

Databricks visualization. Run in Databricks to view.

13.identify the consecutive quarters of sales decline for each product


In [0]:
%sql
with SalesLab as 
(   
  select 
        QTR_ID,
        PRODUCTCODE,
        SUM(SALES) AS TOTAL_SALES,
        LAG(SUM(SALES),1) OVER (partition by PRODUCTCODE ORDER BY QTR_ID) AS PREVIOUS_QUARTER_SALES,
        LAG(SUM(SALES),2) OVER (partition by PRODUCTCODE ORDER BY QTR_ID) AS TWO_QUARTER_AND_SALES
  FROM productssales
  group by QTR_ID,PRODUCTCODE
)
select 
    QTR_ID,
    PRODUCTCODE,
    TOTAL_SALES,
    PREVIOUS_QUARTER_SALES,
    TWO_QUARTER_AND_SALES
from SalesLab 
WHERE TOTAL_SALES < PREVIOUS_QUARTER_SALES AND PREVIOUS_QUARTER_SALES < TWO_QUARTER_AND_SALES
ORDER BY QTR_ID,PRODUCTCODE

QTR_ID PRODUCTCODE TOTAL_SALES PREVIOUS_QUARTER_SALES TWO_QUARTER_AND_SALES 3 S10_4757 15525.760000000002 28118.000000000004 30667.030000000002 3 S10_4962 21557.940000000002 26600.789999999997 29109.129999999997 3 S12_1108 34228.520000000004 36597.58 42518.53999999999 3 S12_1666 22350.920000000002 29229.57 29907.78 3 S12_3148 23269.35 25896.08 30764.62 3 S12_4675 16340.59 21892.25 25090.4 3 S18_1097 20474.579999999998 23156.0 28432.050000000003 3 S18_1749 14919.2 29819.699999999997 31003.16 3 S18_1889 14673.890000000001 16225.439999999999 17179.46 3 S18_2248 4799.64 10000.23 17959.859999999997 3 S18_2325 13524.050000000001 16348.66 30460.029999999995 3 S18_2581 10019.11 17489.59 18735.6 3 S18_2625 8228.619999999999 12995.26 15034.0 3 S18_3029 10859.08 15483.759999999998 18248.27 3 S18_3259 16769.03 17739.88 24010.7 3 S18_4409 10136.92 13545.06 17645.34 3 S18_4668 9242.53 9918.18 18639.32 3 S18_4933 8339.56 9837.11 15081.94 3 S24_1578 18719.699999999997 21513.2 21661.78 3 S24_1937 2879.37 5689.16 15462.119999999999 3 S24_2011 19865.41 26025.84 34986.33 3 S24_2360 11363.2 12182.91 13329.59 3 S24_2840 5671.23 7121.260000000002 17098.75 3 S24_2841 7965.339999999999 10665.319999999998 16273.87 3 S24_2972 5790.74 6539.81 19715.62 3 S24_3151 14678.95 18116.649999999998 20444.36 3 S24_3420 8763.039999999999 11582.62 15153.27 3 S24_3969 3734.99 4433.66 11867.54 3 S24_4278 7637.129999999999 21661.11 22941.870000000003 3 S32_1374 11498.439999999999 24797.560000000005 25114.5 3 S32_2206 5957.73 6027.220000000001 12043.279999999999 3 S50_1341 5944.390000000001 12915.880000000001 13458.29 3 S700_1691 13101.76 17736.350000000002 24714.489999999998 3 S700_2610 10922.099999999999 14139.86 20131.47 3 S700_3505 15601.57 16525.69 29026.560000000005 3 S700_4002 11300.89 15776.04 18535.73 3 S72_1253 7175.469999999999 8809.52 13437.46 3 S72_3212 10040.27 10322.06 19087.5

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
--IDENTIFY TOP 10%  OF PRODUCTS BY SALES IN EACH QUARTER
WITH SALESRANK AS (
  SELECT 
      QTR_ID,
      PRODUCTCODE,
      SALES,
      percent_rank() OVER (PARTITION BY QTR_ID ORDER BY SALES DESC) AS SALES_PERCENT_RANK
  FROM productssales
)
SELECT
    QTR_ID,PRODUCTCODE,SALES
FROM SALESRANK
WHERE SALES_PERCENT_RANK <=0.1
ORDER BY QTR_ID,SALES_PERCENT_RANK

QTR_ID PRODUCTCODE SALES 1 S700_1691 10066.6 1 S24_4278 10039.6 1 S10_4698 9774.03 1 S18_2795 9534.5 1 S18_1342 9240.44 1 S50_1514 8977.05 1 S18_3320 8935.5 1 S18_2248 8884.8 1 S12_1108 8690.36 1 S12_1108 8602.92 1 S12_1666 8470.14 1 S18_2238 8448.64 1 S12_1108 8378.58 1 S24_1937 8344.71 1 S18_4027 8258.0 1 S18_3232 8257.0 1 S10_1949 8254.8 1 S18_4668 7827.3 1 S12_1099 7498.9 1 S18_3482 7397.0 1 S18_3685 7343.9 1 S18_2238 7300.51 1 S18_3232 7264.53 1 S18_4027 7238.28 1 S10_1949 7209.11 1 S10_4757 7208.0 1 S12_1108 7181.44 1 S700_2834 7154.5 1 S18_4027 7031.52 1 S10_4962 7020.48 1 S18_2325 7017.76 1 S12_3148 7016.31 1 S18_2625 6981.0 1 S18_1662 6954.08 1 S12_3891 6952.12 1 S24_3856 6949.67 1 S18_3232 6869.05 1 S18_4721 6862.94 1 S24_2011 6804.63 1 S32_3522 6799.68 1 S24_3856 6763.05 1 S32_1374 6576.5 1 S10_1949 6463.23 1 S10_4962 6426.5 1 S18_3232 6407.86 1 S700_1938 6397.44 1 S18_4027 6376.58 1 S18_3685 6357.6 1 S32_1374 6353.27 1 S24_2011 6341.21 1 S18_3232 6275.72 1 S18_3685 6241.6 1 S10_4962 6231.54 1 S18_2870 6144.6 1 S12_3380 6130.35 1 S10_4698 6123.4 1 S12_3891 6109.29 1 S24_2840 6089.6 1 S12_2823 6087.94 1 S10_1949 6075.3 1 S18_1749 6069.0 1 S10_4698 6065.55 1 S10_4757 5997.6 1 S18_1749 5967.0 1 S12_3148 5958.5 1 S12_2823 5951.44 1 S24_2887 5942.28 2 S18_1749 14082.8 2 S10_1949 12001.0 2 S18_3232 11887.8 2 S10_4698 11886.6 2 S24_3856 11739.7 2 S12_1108 11279.2 2 S12_1108 10606.2 2 S18_3685 10468.9 2 S10_4757 9661.44 2 S10_4698 9264.86 2 S24_3856 9240.0 2 S10_4698 9218.16 2 S12_4675 9048.16 2 S12_1108 8677.8 2 S12_2823 8648.64 2 S24_2300 8498.0 2 S18_1129 8374.69 2 S10_4698 8336.94 2 S18_3232 8289.05 2 S12_2823 8284.0 2 S12_3148 8236.75 2 S18_3232 8209.44 2 S18_1662 8160.3 2 S12_3891 8138.76 2 S12_1666 7969.36 2 S18_2870 7695.6 2 S10_1949 7680.64 2 S12_1099 7599.9 2 S18_1749 7597.3 2 S12_2823 7552.28 2 S700_2466 7543.75 2 S10_1678 7516.08 2 S18_2238 7381.16 2 S12_3148 7366.44 2 S10_1949 7329.06 2 S18_3856 7307.42 2 S18_1097 7182.0 2 S24_2766 7182.0 2 S18_1984 7169.28 2 S18_2238 7146.9 2 S18_3232 7132.68 2 S700_3167 7084.0 2 S18_3232 7083.37 2 S18_4600 7083.0 2 S10_4698 7078.23 2 S18_1589 7048.14 2 S10_4698 7023.9 2 S24_2011 6960.48 2 S18_1662 6916.12 2 S18_4027 6896.75 2 S18_2870 6853.44 2 S18_3232 6773.6 2 S18_4027 6756.0 2 S18_3482 6749.83 2 S18_2238 6712.93 2 S12_1666 6668.24 2 S18_1662 6567.96 3 S10_1949 10993.5 3 S12_1099 9631.0 3 S12_3891 9470.94 3 S12_1099 9245.76 3 S18_2238 9169.0 3 S12_1099 9160.36 3 S18_3482 8427.02 3 S12_1108 8411.56 3 S12_2823 8339.8 3 S18_3232 8331.61 3 S18_2795 8272.34 3 S12_3891 8253.0 3 S12_1108 8023.29 3 S10_1949 8014.82 3 S12_1099 8008.56 3 S12_3891 7962.24 3 S18_2795 7956.46 3 S18_4721 7947.31 3 S10_1949 7374.1 3 S18_4027 7140.76 3 S10_1949 7136.19 3 S18_2238 7110.91 3 S12_1108 7071.27 3 S12_3891 7036.89 3 S10_4698 7023.98 3 S10_4962 7020.64 3 S10_4698 6901.92 3 S12_2823 6863.92 3 S18_3482 6761.6 3 S18_1662 6724.0 3 S18_3140 6695.53 3 S10_4698 6683.34 3 S24_2887 6539.04 3 S18_1129 6499.32 3 S10_2016 6484.59 3 S18_4600 6467.02 3 S18_3232 6401.22 3 S12_1666 6387.8 3 S700_2834 6378.72 3 S24_3856 6336.07 3 S18_2319 6287.66 3 S18_1984 6203.4 3 S24_3432 6168.0 3 S18_3140 6034.33 3 S12_3380 6031.68 3 S18_2238 5938.53 3 S18_1342 5907.5 3 S18_1749 5875.2 3 S18_3232 5852.52 3 S18_1589 5848.68 3 S12_1108 5818.4 4 S18_2325 12536.5 4 S10_1949 11623.7 4 S18_3320 11336.7 4 S24_3151 10758.0 4 S10_1949 10172.7 4 S24_1937 9720.0 4 S700_2824 9558.8 4 S10_1949 9064.89 4 S18_3232 8940.96 4 S10_4698 8892.9 4 S12_1108 8887.7 4 S32_2509 8844.12 4 S18_3232 8754.69 4 S10_4698 8714.7 4 S12_1108 8594.52 4 S12_3148 8378.69 4 S12_1099 8296.35 4 S18_3232 8291.04 4 S32_3522 8209.44 4 S12_2823 8118.55 4 S18_1749 8078.4 4 S10_4698 8065.89 4 S10_1949 8014.82 4 S12_1108 7975.44 4 S18_4721 7901.1 4 S12_3891 7886.2 4 S12_3891 7872.5 4 S10_1678 7737.93 4 S24_3856 7723.5 4 S10_4698 7667.14 4 S18_1749 7650.0 4 S18_3232 7620.5 4 S18_1749 7554.8 4 S18_2795 7492.4 4 S18_1984 7488.04 4 S18_1662 7483.98 4 S12_1108 7474.5 4 S18_223

CATEGORIES SALES PERFORMANCE AS 'HIGH','LOW','MEDIUM' BASED ON PERCENTILES

In [0]:
%sql
WITH PERC_TAB AS (
  SELECT 
      QTR_ID,
      PRODUCTCODE,
      SALES,
      NTILE(100) OVER(PARTITION BY QTR_ID ORDER BY SALES DESC) AS PERCENTILE
  from productssales
)

SELECT
    QTR_ID,
    PRODUCTCODE,
    SALES,
    CASE 
        WHEN PERCENTILE <=25 THEN 'LOW'
        WHEN PERCENTILE BETWEEN 25 AND 75 THEN 'MEDIUM'
        ELSE 'HIGH'
  END AS PERFORMANCE_CATEGORY
FROM PERC_TAB
ORDER BY QTR_ID,PRODUCTCODE

QTR_ID PRODUCTCODE SALES PERFORMANCE_CATEGORY 1 S10_1678 733.11 HIGH 1 S10_1678 3207.12 MEDIUM 1 S10_1678 3965.66 MEDIUM 1 S10_1678 4708.44 LOW 1 S10_1678 2871.0 MEDIUM 1 S10_1949 2416.56 MEDIUM 1 S10_1949 6075.3 LOW 1 S10_1949 6463.23 LOW 1 S10_1949 4514.92 LOW 1 S10_1949 7209.11 LOW 1 S10_1949 8254.8 LOW 1 S10_1949 5404.62 LOW 1 S10_2016 3896.49 MEDIUM 1 S10_2016 5422.39 LOW 1 S10_2016 5288.01 LOW 1 S10_2016 3009.09 MEDIUM 1 S10_2016 2225.5 MEDIUM 1 S10_4698 3664.1 MEDIUM 1 S10_4698 3834.38 MEDIUM 1 S10_4698 6065.55 LOW 1 S10_4698 9774.03 LOW 1 S10_4698 1822.17 HIGH 1 S10_4698 6123.4 LOW 1 S10_4757 5197.92 LOW 1 S10_4757 4846.7 LOW 1 S10_4757 5997.6 LOW 1 S10_4757 7208.0 LOW 1 S10_4757 3370.56 MEDIUM 1 S10_4757 4046.25 MEDIUM 1 S10_4962 2297.05 MEDIUM 1 S10_4962 6231.54 LOW 1 S10_4962 7020.48 LOW 1 S10_4962 1735.3 HIGH 1 S10_4962 5398.26 LOW 1 S10_4962 6426.5 LOW 1 S12_1099 4517.91 LOW 1 S12_1099 3420.0 MEDIUM 1 S12_1099 2817.87 MEDIUM 1 S12_1099 5265.15 LOW 1 S12_1099 7498.9 LOW 1 S12_1099 2575.04 MEDIUM 1 S12_1108 8378.58 LOW 1 S12_1108 8602.92 LOW 1 S12_1108 7181.44 LOW 1 S12_1108 8690.36 LOW 1 S12_1108 2280.96 MEDIUM 1 S12_1108 3823.64 MEDIUM 1 S12_1108 3560.64 MEDIUM 1 S12_1666 5759.42 LOW 1 S12_1666 3451.0 MEDIUM 1 S12_1666 2464.8 MEDIUM 1 S12_1666 3415.44 MEDIUM 1 S12_1666 2952.0 MEDIUM 1 S12_1666 3394.98 MEDIUM 1 S12_1666 8470.14 LOW 1 S12_2823 3036.6 MEDIUM 1 S12_2823 5951.44 LOW 1 S12_2823 6087.94 LOW 1 S12_2823 4771.8 LOW 1 S12_2823 3867.08 MEDIUM 1 S12_2823 3877.06 MEDIUM 1 S12_3148 5862.0 LOW 1 S12_3148 4071.85 MEDIUM 1 S12_3148 4713.6 LOW 1 S12_3148 7016.31 LOW 1 S12_3148 3142.36 MEDIUM 1 S12_3148 5958.5 LOW 1 S12_3380 1809.5 HIGH 1 S12_3380 3288.82 MEDIUM 1 S12_3380 3987.2 MEDIUM 1 S12_3380 2495.5 MEDIUM 1 S12_3380 4946.76 LOW 1 S12_3380 6130.35 LOW 1 S12_3891 6109.29 LOW 1 S12_3891 6952.12 LOW 1 S12_3891 3114.4 MEDIUM 1 S12_3891 4566.05 LOW 1 S12_3891 5045.22 LOW 1 S12_3891 5941.5 LOW 1 S12_3891 3241.9 MEDIUM 1 S12_3990 2775.08 MEDIUM 1 S12_3990 2529.36 MEDIUM 1 S12_3990 1627.92 HIGH 1 S12_3990 2591.96 MEDIUM 1 S12_3990 3485.82 MEDIUM 1 S12_3990 2864.17 MEDIUM 1 S12_4473 4891.68 LOW 1 S12_4473 4521.96 LOW 1 S12_4473 4615.78 LOW 1 S12_4473 1749.79 HIGH 1 S12_4473 2130.56 MEDIUM 1 S12_4675 5243.79 LOW 1 S12_4675 4068.7 MEDIUM 1 S12_4675 4180.44 MEDIUM 1 S12_4675 3731.04 MEDIUM 1 S12_4675 2684.43 MEDIUM 1 S12_4675 5182.0 LOW 1 S18_1097 5152.0 LOW 1 S18_1097 3911.49 MEDIUM 1 S18_1097 4704.0 LOW 1 S18_1097 3360.0 MEDIUM 1 S18_1097 2467.9 MEDIUM 1 S18_1097 4916.66 LOW 1 S18_1097 3920.0 MEDIUM 1 S18_1129 4529.28 LOW 1 S18_1129 5895.05 LOW 1 S18_1129 4186.73 MEDIUM 1 S18_1129 2611.8 MEDIUM 1 S18_1129 4379.18 MEDIUM 1 S18_1129 3375.72 MEDIUM 1 S18_1342 4808.31 LOW 1 S18_1342 2515.32 MEDIUM 1 S18_1342 2413.26 MEDIUM 1 S18_1342 3288.78 MEDIUM 1 S18_1342 2953.75 MEDIUM 1 S18_1342 9240.44 LOW 1 S18_1342 5548.9 LOW 1 S18_1367 2354.88 MEDIUM 1 S18_1367 3156.16 MEDIUM 1 S18_1367 2055.74 HIGH 1 S18_1367 1320.75 HIGH 1 S18_1367 1504.12 HIGH 1 S18_1367 1423.29 HIGH 1 S18_1367 4998.0 LOW 1 S18_1589 4492.36 LOW 1 S18_1589 1449.76 HIGH 1 S18_1589 5433.08 LOW 1 S18_1589 4161.38 MEDIUM 1 S18_1589 2758.7 MEDIUM 1 S18_1662 1364.25 HIGH 1 S18_1662 4215.09 MEDIUM 1 S18_1662 1611.4 HIGH 1 S18_1662 5719.5 LOW 1 S18_1662 6954.08 LOW 1 S18_1662 5279.4 LOW 1 S18_1749 5967.0 LOW 1 S18_1749 6069.0 LOW 1 S18_1749 5399.55 LOW 1 S18_1749 3712.8 MEDIUM 1 S18_1749 5151.0 LOW 1 S18_1749 4703.81 LOW 1 S18_1889 1339.8 HIGH 1 S18_1889 3686.54 MEDIUM 1 S18_1889 3039.96 MEDIUM 1 S18_1889 3881.78 MEDIUM 1 S18_1889 2100.56 HIGH 1 S18_1889 3130.82 MEDIUM 1 S18_1984 4432.7 LOW 1 S18_1984 3892.08 MEDIUM 1 S18_1984 4840.87 LOW 1 S18_1984 4207.84 MEDIUM 1 S18_1984 4352.76 MEDIUM 1 S18_1984 1463.7 HIGH 1 S18_2238 8448.64 LOW 1 S18_2238 7300.51 LOW 1 S18_2238 2602.25 MEDIUM 1 S18_2238 3457.92 MEDIUM 1 S18_2238 2200.0 MEDIUM 1 S18_2248 3390.0 MEDIUM 1 S18_2248 1423.8 HIGH 1 S18_2248 1322.16 HIGH 1 S18_2248 8884.8 LOW 1 S18_2248 1608.0 HIGH 1 S18_2248 1331.1 HIGH 1

MONTH WITH HIGHEST SALES IN EACH YEAR

In [0]:
%sql
SELECT YEAR_ID,MONTH_ID,TOTAL_SALES,RANK 
FROM (SELECT YEAR_ID,MONTH_ID,TOTAL_SALES,DENSE_RANK() OVER(PARTITION BY YEAR_ID ORDER BY TOTAL_SALES DESC)
AS RANK FROM (
    SELECT YEAR_ID,MONTH_ID,SUM(SALES) AS TOTAL_SALES FROM productssales group by YEAR_ID,MONTH_ID
    ) AS AGGREGATEDSALES
) AS RANKEDSALES
WHERE RANK = 1 ORDER BY YEAR_ID,MONTH_ID

YEAR_ID MONTH_ID TOTAL_SALES RANK 2003 11 1029837.6600000001 1 2004 11 1089048.0100000005 1 2005 5 457861.05999999965 1